In [2]:
import pandas as pd

# display all pandas columns
pd.set_option('display.max_columns', None)  # Show all columns

## Data import

In [3]:
df_traffic_data = pd.read_excel('../../data/raw/traffic_sensors_locations/all_sensors.xlsx') 
df_air_quality_and_locations = pd.read_parquet("../../data/processed/air/df_air_quality_and_locations_from_2013.parquet")

In [4]:
len(df_traffic_data)

5095

In [5]:
len(df_traffic_data.drop_duplicates(subset=['longitud', 'latitud']))

4941

In [6]:
len(df_air_quality_and_locations)

2490936

In [7]:
len(df_air_quality_and_locations.drop_duplicates(subset=["LONGITUD", "LATITUD"]))

24

## Visualization

In [8]:
import folium

# Remove duplicates for air quality data
df_air_quality_and_locations = df_air_quality_and_locations.drop_duplicates(subset=["LONGITUD", "LATITUD"])

# Remove duplicates for traffic data
df_traffic_data = df_traffic_data.drop_duplicates(subset=['longitud', 'latitud'])  # Assuming 'id' is the identifier for the traffic sensor

# Create a map centered around the average coordinates of the NO2 sensors
map_center = [df_air_quality_and_locations["LATITUD"].mean(), df_air_quality_and_locations["LONGITUD"].mean()]
m = folium.Map(location=map_center, zoom_start=12)

# Add CircleMarkers for NO2 sensors
for _, row in df_air_quality_and_locations.iterrows():
    folium.CircleMarker(
        location=[row["LATITUD"], row["LONGITUD"]],
        radius=8,  # Size of the circle
        color='blue',  # Color for NO2 sensors
        fill=True,
        fill_color='blue',
        fill_opacity=0.9,
        popup=f'Sensor NO2: {row["LONGITUD"]}, {row["LATITUD"]}'
    ).add_to(m)

# Add CircleMarkers for traffic sensors
for _, row in df_traffic_data.iterrows():
    folium.CircleMarker(
        location=[row["latitud"], row["longitud"]],
        radius=2,  # Size of the circle
        color='red',  # Color for traffic sensors
        fill=True,
        fill_color='red',
        fill_opacity=0.1,
        popup=f'Sensor Traffic: {row["id"]}, {row["latitud"]}, {row["longitud"]}'
    ).add_to(m)

# Display the map
m

## Mapear Sensores de NO2 con sensores de Trafico

`Para ello, como primera iteracion, nos quedaremos solo con los sensores de NO2 que tengan al menos un sensor de trafico en el radio de 200 metros. En el caso de que no haya sensores, no usaremos ese sensor de NO2. En el caso de que haya mas de uno, usaremos los valores intercuartiles.`

In [9]:
#porque antes he eliminado duplicados...
df_traffic_data = pd.read_excel('../../data/raw/traffic_sensors_locations/all_sensors.xlsx') 

In [10]:
df_air_quality_and_locations = df_air_quality_and_locations[['CODIGO','LATITUD','LONGITUD']]
df_traffic_data = df_traffic_data[['id','latitud','longitud']]

df_air_quality_and_locations = df_air_quality_and_locations.rename(columns={'CODIGO':'id_no2'})
df_traffic_data = df_traffic_data.rename(columns={'id':'id_trafico'})

df_air_quality_and_locations['id_no2'] = df_air_quality_and_locations['id_no2'].astype(str)
df_traffic_data['id_trafico'] = df_traffic_data['id_trafico'].astype(str)

In [11]:
import pandas as pd
import numpy as np
from scipy.spatial import cKDTree

# ------------------------
# 2. Convertir coordenadas a radianes
# ------------------------
df_air_quality_and_locations[['latitud_rad', 'longitud_rad']] = np.radians(df_air_quality_and_locations[['LATITUD', 'LONGITUD']])
df_traffic_data[['latitud_rad', 'longitud_rad']] = np.radians(df_traffic_data[['latitud', 'longitud']])

# ------------------------
# 3. Construcción del KDTree para búsqueda eficiente
# ------------------------
tree = cKDTree(df_traffic_data[['latitud_rad', 'longitud_rad']])

# Definir radio en radianes (200m ≈ 0.0018 rad)
radio = 200 / 6371000  # Radio de la Tierra en metros

# ------------------------
# 4. Asignación de sensores de tráfico a cada sensor de NO2
# ------------------------
asignaciones = []

for i, row in df_air_quality_and_locations.iterrows():
    idx_cercanos = tree.query_ball_point([row['latitud_rad'], row['longitud_rad']], radio)
    
    for idx in idx_cercanos:
        distance = round(tree.query([row['latitud_rad'], row['longitud_rad']], k=1)[0] * 6371000)  # Convert from radians to meters
        
        asignaciones.append({
            'id_no2': row['id_no2'],
            'id_trafico': df_traffic_data.iloc[idx]['id_trafico'],
            'distance_m': distance,  # New column for distance
            'latitud_no2': row['LATITUD'],  # Latitude from df_air_quality_and_locations
            'longitud_no2': row['LONGITUD'],  # Longitude from df_air_quality_and_locations
            'latitud_trafico': df_traffic_data.iloc[idx]['latitud'],  # Latitude from df_traffic_data
            'longitud_trafico': df_traffic_data.iloc[idx]['longitud']   # Longitude from df_traffic_data
        })

df_mapping_no2_to_traffic = pd.DataFrame(asignaciones)

In [23]:
df_mapping_no2_to_traffic.to_csv("no2_y_traffic_filtered_by_proximity.csv", index = False)

In [24]:
df_mapping_no2_to_traffic

id_no2 id_trafico  distance_m  latitud_no2  longitud_no2  \
0   28079004      10647          71    40.423882     -3.712257   
1   28079004       4333          71    40.423882     -3.712257   
2   28079004       4313          71    40.423882     -3.712257   
3   28079004       4285          71    40.423882     -3.712257   
4   28079004       3732          71    40.423882     -3.712257   
..       ...        ...         ...          ...           ...   
66  28079056       6822          24    40.385034     -3.718768   
67  28079056      10332          24    40.385034     -3.718768   
68  28079056      10848          24    40.385034     -3.718768   
69  28079056      10849          24    40.385034     -3.718768   
70  28079056      11006          24    40.385034     -3.718768   

    latitud_trafico  longitud_trafico  
0           40.4238           -3.7139  
1           40.4222           -3.7128  
2           40.4224           -3.7126  
3           40.4232           -3.7115  
4           40.4235           -3.7129  
..              ...               ...  
66          40.3847           -3.7178  
67          40.3846           -3.7177  
68          40.3848           -3.7182  
69          40.3858           -3.7174  
70          40.3859           -3.7172  

[71 rows x 7 columns]

In [22]:
import folium
import random

# Create a map centered around the average latitude and longitude
map_center = [df_mapping_no2_to_traffic['latitud_no2'].mean(), df_mapping_no2_to_traffic['longitud_no2'].mean()]
m = folium.Map(location=map_center, zoom_start=12)

# Generate a list of colors for the NO2 sensors
colors = ['blue', 'green', 'orange', 'purple', 'darkred', 'lightred', 'beige', 'darkblue', 'darkgreen', 'cadetblue', 'pink', 'lightblue']

# Dictionary to hold the color for each NO2 sensor
no2_colors = {}

# Add markers for NO2 sensors with unique colors
for _, row in df_mapping_no2_to_traffic.iterrows():
    if row['id_no2'] not in no2_colors:
        # Assign a random color from the list
        color = random.choice(colors)
        no2_colors[row['id_no2']] = color
    
    # Add a circle marker for NO2 sensors
    folium.CircleMarker(
        location=[row['latitud_no2'], row['longitud_no2']],
        radius=8,
        color=no2_colors[row['id_no2']],
        fill=True,
        fill_opacity=0.6,
        popup=f"NO2 Sensor ID: {row['id_no2']}",
        tooltip=f"NO2 Sensor ID: {row['id_no2']}"
    ).add_to(m)

# Add markers for Traffic data with the same color as the corresponding NO2 sensor
for _, row in df_mapping_no2_to_traffic.iterrows():
    folium.Marker(
        location=[row['latitud_trafico'], row['longitud_trafico']],
        popup=f"Traffic ID: {row['id_trafico']}, NO2 ID: {row['id_no2']}",
        icon=folium.Icon(color=no2_colors[row['id_no2']], icon='info-sign')  # Use the same color as NO2 sensor
    ).add_to(m)

# Save the map to an HTML file or display it directly
m